# 5D Kerr-AdS spacetime with a Nambu-Goto string

## Case b = n a

This [SageMath](https://www.sagemath.org/) notebook is relative to the article *Heavy quarks in rotating plasma via holography* by Anastasia A. Golubtsova, Eric Gourgoulhon and Marina K. Usova, [arXiv:2107.11672](https://arxiv.org/abs/2107.11672).

The involved differential geometry computations are based on tools developed through the [SageManifolds](https://sagemanifolds.obspm.fr) project.

*NB:* a version of SageMath at least equal to 9.1 is required to run this notebook:

In [1]:
version()

'SageMath version 9.3, Release Date: 2021-05-09'

First we set up the notebook to display mathematical objects using LaTeX rendering:

In [2]:
%display latex

Since some computations are quite long, we ask for running them in parallel on 8 cores:

In [3]:
Parallelism().set(nproc=8)

## Spacetime manifold

We declare the Kerr-AdS spacetime as a 5-dimensional Lorentzian manifold:

In [4]:
M = Manifold(5, 'M', r'\mathcal{M}', structure='Lorentzian', metric_name='G')
print(M)

5-dimensional Lorentzian manifold M


Let us define **Boyer-Lindquist-type coordinates (rational polynomial version)** on $\mathcal{M}$, via the method `chart()`, the argument of which is a string expressing the coordinates names, their ranges (the default is $(-\infty,+\infty)$) and their LaTeX symbols:

In [5]:
BL.<t,r,mu,ph,ps> = M.chart(r't r:(0,+oo) mu:(0,1):\mu ph:(0,2*pi):\phi ps:(0,2*pi):\psi')
BL

Chart (M, (t, r, mu, ph, ps))

The coordinate $\mu$ is related to the standard Boyer-Lindquist coordinate $\theta$ by
$$ \mu = \cos\theta$$

The coordinate ranges are

In [6]:
BL.coord_range()

t: (-oo, +oo); r: (0, +oo); mu: (0, 1); ph: (0, 2*pi); ps: (0, 2*pi)

Note that contrary to the 4-dimensional case, the range of $\mu$ is $(0,1)$ only (cf. Sec. 1.2 of [R.C. Myers, arXiv:1111.1903](https://arxiv.org/abs/1111.1903) or Sec. 2 of [G.W. Gibbons, H. Lüb, Don N. Page, C.N. Pope, J. Geom. Phys. **53**, 49 (2005)](https://doi.org/10.1016/j.geomphys.2004.05.001)). In other words, the range of $\theta$ is $\left(0, \frac{\pi}{2}\right)$ only. 

## Metric tensor

The 4 parameters $m$, $a$, $b$ and $\ell$ of the Kerr-AdS spacetime are declared as symbolic variables, $a$ and $b$ being the two angular momentum parameters and $\ell$ being related to the cosmological constant by $\Lambda = - 6 \ell^2$:

In [7]:
var('m a b', domain='real')

(m, a, b)

In [8]:
var('l', domain='real', latex_name=r'\ell')

l

We assume that $b = n a$:

In [9]:
n = var('n', domain='real')
b = n*a

Some auxiliary functions:

In [10]:
keep_Delta = True  # change to False to provide explicit expression for Delta_r, Xi_a, etc...

In [11]:
sig = (1 + r^2*l^2)/r^2
costh2 = mu^2
sinth2 = 1 - mu^2
rho2 = r^2 + a^2*mu^2 + b^2*sinth2
# Explicit expressions:
Delta_r_expr = (r^2+a^2)*(r^2+b^2)*sig - 2*m
Delta_th_expr = 1 - a^2*l^2*costh2 - b^2*l^2*sinth2
Xi_a_expr = 1 - a^2*l^2
Xi_b_expr = 1 - b^2*l^2
if keep_Delta:
    Delta_r = var('Delta_r', latex_name=r'\Delta_r', domain='real')
    Delta_th = var('Delta_th', latex_name=r'\Delta_\theta', domain='real')
    if a == b:
        Xi_a = var('Xi', latex_name=r'\Xi', domain='real')
        Xi_b = Xi_a
    else:
        Xi_a = var('Xi_a', latex_name=r'\Xi_a', domain='real')
        Xi_b = var('Xi_b', latex_name=r'\Xi_b', domain='real')
else:
    Delta_r = Delta_r_expr
    Delta_th = Delta_th_expr
    Xi_a = Xi_a_expr
    Xi_b = Xi_b_expr

The metric is set by its components in the coordinate frame associated with the Boyer-Lindquist-type coordinates, which is the current manifold's default frame. These components can be deduced from
Eq. (5.22) of the article [S.W. Hawking, C.J. Hunter & M.M. Taylor-Robinson, Phys. Rev. D **59**, 064005 (1999)](https://doi.org/10.1103/PhysRevD.59.064005) (the check of agreement with this equation is performed below):

In [12]:
G = M.metric()
tmp = 1/rho2*( -Delta_r + Delta_th*(a^2*sinth2 + b^2*mu^2) + a^2*b^2*sig )
G[0,0] = tmp.simplify_full()
tmp = a*sinth2/(rho2*Xi_a)*( Delta_r - (r^2+a^2)*(Delta_th + b^2*sig) )
G[0,3] = tmp.simplify_full()
tmp = b*mu^2/(rho2*Xi_b)*( Delta_r - (r^2+b^2)*(Delta_th + a^2*sig) )
G[0,4] = tmp.simplify_full()
G[1,1] = (rho2/Delta_r).simplify_full()
G[2,2] = (rho2/Delta_th/(1-mu^2)).simplify_full()
tmp = sinth2/(rho2*Xi_a^2)*( - Delta_r*a^2*sinth2 + (r^2+a^2)^2*(Delta_th + sig*b^2*sinth2) ) 
G[3,3] = tmp.simplify_full()
tmp = a*b*sinth2*mu^2/(rho2*Xi_a*Xi_b)*( - Delta_r + sig*(r^2+a^2)*(r^2+b^2) )
G[3,4] = tmp.simplify_full()
tmp = mu^2/(rho2*Xi_b^2)*( - Delta_r*b^2*mu^2 + (r^2+b^2)^2*(Delta_th + sig*a^2*mu^2) )
G[4,4] = tmp.simplify_full()

In [13]:
G.display_comp(only_nonredundant=True)

G_t,t = (a^4*n^2 - (Delta_th*a^2*mu^2 - Delta_th*a^2 - (a^4*l^2 + Delta_th*a^2*mu^2)*n^2 + Delta_r)*r^2)/(r^4 + (a^2*mu^2 - (a^2*mu^2 - a^2)*n^2)*r^2) 
G_t,ph = ((Delta_th*a*mu^2 + (a^3*l^2*mu^2 - a^3*l^2)*n^2 - Delta_th*a)*r^4 + (a^5*mu^2 - a^5)*n^2 - (Delta_th*a^3 - (Delta_th*a^3 - Delta_r*a)*mu^2 + (a^5*l^2 + a^3 - (a^5*l^2 + a^3)*mu^2)*n^2 - Delta_r*a)*r^2)/(Xi_a*r^4 + (Xi_a*a^2*mu^2 - (Xi_a*a^2*mu^2 - Xi_a*a^2)*n^2)*r^2) 
G_t,ps = -(a^5*mu^2*n^3 + (a^3*l^2 + Delta_th*a)*mu^2*n*r^4 + ((a^5*l^2 + Delta_th*a^3)*mu^2*n^3 + (a^3 - Delta_r*a)*mu^2*n)*r^2)/(Xi_b*r^4 + (Xi_b*a^2*mu^2 - (Xi_b*a^2*mu^2 - Xi_b*a^2)*n^2)*r^2) 
G_r,r = (a^2*mu^2 - (a^2*mu^2 - a^2)*n^2 + r^2)/Delta_r 
G_mu,mu = -(a^2*mu^2 - (a^2*mu^2 - a^2)*n^2 + r^2)/(Delta_th*mu^2 - Delta_th) 
G_ph,ph = -((Delta_th*mu^2 - (a^2*l^2*mu^4 - 2*a^2*l^2*mu^2 + a^2*l^2)*n^2 - Delta_th)*r^6 + (2*Delta_th*a^2*mu^2 - 2*Delta_th*a^2 - (2*a^4*l^2 + (2*a^4*l^2 + a^2)*mu^4 - 2*(2*a^4*l^2 + a^2)*mu^2 + a^2)*n^2)*r^4 - (a^6*mu^4 - 2*a^6*mu^2 + a^6)*n^2 + (Delta_r*a^2*mu^4 - Delta_th*a^4 + Delta_r*a^2 + (Delta_th*a^4 - 2*Delta_r*a^2)*mu^2 - (a^6*l^2 + (a^6*l^2 + 2*a^4)*mu^4 + 2*a^4 - 2*(a^6*l^2 + 2*a^4)*mu^2)*n^2)*r^2)/(Xi_a^2*r^4 + (Xi_a^2*a^2*mu^2 - (Xi_a^2*a^2*mu^2 - Xi_a^2*a^2)*n^2)*r^2) 
G_ph,ps = -((a^2*l^2*mu^4 - a^2*l^2*mu^2)*n*r^6 + ((a^4*l^2*mu^4 - a^4*l^2*mu^2)*n^3 + ((a^4*l^2 + a^2)*mu^4 - (a^4*l^2 + a^2)*mu^2)*n)*r^4 + (a^6*mu^4 - a^6*mu^2)*n^3 + (((a^6*l^2 + a^4)*mu^4 - (a^6*l^2 + a^4)*mu^2)*n^3 + ((a^4 - Delta_r*a^2)*mu^4 - (a^4 - Delta_r*a^2)*mu^2)*n)*r^2)/(Xi_a*Xi_b*r^4 + (Xi_a*Xi_b*a^2*mu^2 - (Xi_a*Xi_b*a^2*mu^2 - Xi_a*Xi_b*a^2)*n^2)*r^2) 
G_ps,ps = (a^6*mu^4*n^4 + (a^2*l^2*mu^4 + Delta_th*mu^2)*r^6 + (a^2*mu^4 + 2*(a^4*l^2*mu^4 + Delta_th*a^2*mu^2)*n^2)*r^4 + ((2*a^4 - Delta_r*a^2)*mu^4*n^2 + (a^6*l^2*mu^4 + Delta_th*a^4*mu^2)*n^4)*r^2)/(Xi_b^2*r^4 + (Xi_b^2*a^2*mu^2 - (Xi_b^2*a^2*mu^2 - Xi_b^2*a^2)*n^2)*r^2)

### Check of Eq. (2.9)

We need the 1-forms $\mathrm{d}t$, $\mathrm{d}r$, $\mathrm{d}\mu$, $\mathrm{d}\phi$ and $\mathrm{d}\psi$:

In [14]:
dt, dr, dmu, dph, dps = (BL.coframe()[i] for i in M.irange())
dt, dr, dmu, dph, dps

(1-form dt on the 5-dimensional Lorentzian manifold M,
 1-form dr on the 5-dimensional Lorentzian manifold M,
 1-form dmu on the 5-dimensional Lorentzian manifold M,
 1-form dph on the 5-dimensional Lorentzian manifold M,
 1-form dps on the 5-dimensional Lorentzian manifold M)

In [15]:
print(dt)

1-form dt on the 5-dimensional Lorentzian manifold M


In agreement with $\mu = \cos\theta$, we introduce the 1-form
$$\mathrm{d}\theta = - \mathrm{d}\mu /\sin\theta ,$$
with
$\sin\theta = \sqrt{1-\mu^2}$ since $\theta\in\left(0, \frac{\pi}{2}\right)$ :

In [16]:
dth = - 1/sqrt(1 - mu^2)*dmu

In [17]:
s1 = dt - a*sinth2/Xi_a*dph - b*costh2/Xi_b*dps
s1.display()

dt + (a*mu^2 - a)/Xi_a dph - a*mu^2*n/Xi_b dps

In [18]:
s2 = a*dt - (r^2 + a^2)/Xi_a*dph
s2.display()

a dt - (a^2 + r^2)/Xi_a dph

In [19]:
s3 = b*dt - (r^2 + b^2)/Xi_b*dps
s3.display()

a*n dt - (a^2*n^2 + r^2)/Xi_b dps

In [20]:
s4 = a*b*dt - b*(r^2 + a^2)*sinth2/Xi_a * dph - a*(r^2 + b^2)*costh2/Xi_b * dps
s4.display()

a^2*n dt + ((a*mu^2 - a)*n*r^2 + (a^3*mu^2 - a^3)*n)/Xi_a dph - (a^3*mu^2*n^2 + a*mu^2*r^2)/Xi_b dps

In [21]:
G0 = - Delta_r/rho2 * s1*s1 + Delta_th*sinth2/rho2 * s2*s2 \
     + Delta_th*costh2/rho2 * s3*s3 + rho2/Delta_r * dr*dr \
     + rho2/Delta_th * dth*dth + sig/rho2 * s4*s4

Check of Eq. (2.9):

In [22]:
G0 == G

True

## Einstein equation

The Ricci tensor of $g$ is

In [23]:
if not keep_Delta:
    # Ric = G.ricci()
    # print(Ric)
    pass

In [24]:
if not keep_Delta:
    # show(Ric.display_comp(only_nonredundant=True))
    pass

Let us check that $g$ is a solution of the vacuum Einstein equation with the cosmological constant $\Lambda = - 6 \ell^2$:

In [25]:
Lambda = -6*l^2
if not keep_Delta:
    # print(Ric == 2/3*Lambda*G)
    pass

## String worldsheet

The string worldsheet as a 2-dimensional Lorentzian submanifold of $\mathcal{M}$:

In [26]:
W = Manifold(2, 'W', ambient=M, structure='Lorentzian', 
             latex_name=r'\mathcal{W}')
print(W)

2-dimensional Lorentzian submanifold W immersed in the 5-dimensional Lorentzian manifold M


Let us assume that the string worldsheet is parametrized by $(t,r)$:

In [27]:
XW.<t,r> = W.chart(r't r:(0,+oo)')
XW

Chart (W, (t, r))

The string embedding in Kerr-AdS spacetime, as an expansion about a 
straight string solution in AdS (Eq. (4.5) of the paper):

In [28]:
Mu0 = var('Mu0', latex_name=r'\mu_0', domain='real')
Phi0 = var('Phi0', latex_name=r'\Phi_0', domain='real')
Psi0 = var('Psi0', latex_name=r'\Psi_0', domain='real')

cosTh0 = Mu0
sinTh0 = sqrt(1 - Mu0^2)

mu_s = Mu0 + (a+b)^2*function('mu_1')(r)
ph_s = Phi0 + a*l^2*t + a*function('phi_1')(r)
ps_s = Psi0 + b*l^2*t + b*function('psi_1')(r)

F = W.diff_map(M, {(XW, BL): [t, r, mu_s, ph_s, ps_s]}, name='F') 

W.set_embedding(F)

F.display()

F: W --> M
   (t, r) |--> (t, r, mu, ph, ps) = (t, r, (a*n + a)^2*mu_1(r) + Mu0, a*l^2*t + a*phi_1(r) + Phi0, a*l^2*n*t + a*n*psi_1(r) + Psi0)

In [29]:
F.jacobian_matrix()

[                                         1                                          0]
[                                         0                                          1]
[                                         0 (a^2*n^2 + 2*a^2*n + a^2)*diff(mu_1(r), r)]
[                                     a*l^2                        a*diff(phi_1(r), r)]
[                                   a*l^2*n                      a*n*diff(psi_1(r), r)]

### Induced metric on the string worldsheet

Because of the bug [#27492](https://trac.sagemath.org/ticket/27492), which impedes parallel computations involving symbolic functions, such as $\mu_1$, we switch back to serial computations:

In [30]:
Parallelism().set(nproc=1)

The metric on the string worldsheet $\mathcal{W}$ is the metric $g$ induced by the spacetime metric $G$, i.e. the pullback of $G$ by the embedding $F$:

In [31]:
g = W.induced_metric()

## Nambu-Goto action

The determinant of $g$ is

In [32]:
detg = g.determinant().expr()

Expanding at fourth order in $a$ (will be required latter):

In [33]:
detg_a4 = detg.series(a, 5).truncate().simplify_full()

In [34]:
detg_a40 = detg_a4

In [35]:
detg_a4 = detg_a40

In [36]:
detg_a4 = detg_a4.subs({Xi_a: Xi_a_expr, Xi_b: Xi_b_expr, 
                        Delta_r: Delta_r_expr, Delta_th: Delta_th_expr})
detg_a4 = detg_a4.subs({mu: mu_s})

In [37]:
detg_a4 = detg_a4.series(a, 5).truncate().simplify_full()

In [38]:
detg_a4.variables()

(Mu0, a, l, m, n, r)

For the time being, only the expansion at second order in $a$ is required:

In [39]:
detg_a2 = detg_a4.series(a, 3).truncate().simplify_full()

The Nambu-Goto Lagrangian at second order in $a$:

In [40]:
L_a2 = (sqrt(-detg_a2)).series(a, 3).truncate().simplify_full()
L_a2

-1/2*((3*Mu0^2*a^2*l^4*n^2 - 3*(Mu0^2 - 1)*a^2*l^4 - 2*l^2)*r^4 - (Mu0^2 - 1)*a^2 - (4*Mu0^2*a^2*l^2*m - Mu0^2*a^2)*n^2 + ((Mu0^2 - 1)*a^2*l^4*r^8 + 2*(Mu0^2 - 1)*a^2*l^2*r^6 - 4*(Mu0^2 - 1)*a^2*m*r^2 + 4*(Mu0^2 - 1)*a^2*m^2 - (4*(Mu0^2 - 1)*a^2*l^2*m - (Mu0^2 - 1)*a^2)*r^4)*diff(phi_1(r), r)^2 - (Mu0^2*a^2*l^4*n^2*r^8 + 2*Mu0^2*a^2*l^2*n^2*r^6 - 4*Mu0^2*a^2*m*n^2*r^2 + 4*Mu0^2*a^2*m^2*n^2 - (4*Mu0^2*a^2*l^2*m - Mu0^2*a^2)*n^2*r^4)*diff(psi_1(r), r)^2 + 4*((Mu0^2 - 1)*a^2*l^2 + 1)*m - 2*r^2)/(l^2*r^4 + r^2 - 2*m)

In [41]:
L_a2.numerator()

Mu0^2*a^2*l^4*n^2*r^8*diff(psi_1(r), r)^2 - Mu0^2*a^2*l^4*r^8*diff(phi_1(r), r)^2 + a^2*l^4*r^8*diff(phi_1(r), r)^2 + 2*Mu0^2*a^2*l^2*n^2*r^6*diff(psi_1(r), r)^2 - 4*Mu0^2*a^2*l^2*m*n^2*r^4*diff(psi_1(r), r)^2 - 3*Mu0^2*a^2*l^4*n^2*r^4 - 2*Mu0^2*a^2*l^2*r^6*diff(phi_1(r), r)^2 + 4*Mu0^2*a^2*l^2*m*r^4*diff(phi_1(r), r)^2 + 3*Mu0^2*a^2*l^4*r^4 + 2*a^2*l^2*r^6*diff(phi_1(r), r)^2 + Mu0^2*a^2*n^2*r^4*diff(psi_1(r), r)^2 - 4*a^2*l^2*m*r^4*diff(phi_1(r), r)^2 - 4*Mu0^2*a^2*m*n^2*r^2*diff(psi_1(r), r)^2 - 3*a^2*l^4*r^4 - Mu0^2*a^2*r^4*diff(phi_1(r), r)^2 + 4*Mu0^2*a^2*m^2*n^2*diff(psi_1(r), r)^2 + 4*Mu0^2*a^2*l^2*m*n^2 + 4*Mu0^2*a^2*m*r^2*diff(phi_1(r), r)^2 - 4*Mu0^2*a^2*m^2*diff(phi_1(r), r)^2 + a^2*r^4*diff(phi_1(r), r)^2 - 4*Mu0^2*a^2*l^2*m - 4*a^2*m*r^2*diff(phi_1(r), r)^2 - Mu0^2*a^2*n^2 + 2*l^2*r^4 + 4*a^2*m^2*diff(phi_1(r), r)^2 + 4*a^2*l^2*m + Mu0^2*a^2 - a^2 + 2*r^2 - 4*m

In [42]:
L_a2.denominator()

2*l^2*r^4 + 2*r^2 - 4*m

###  Euler-Lagrange equations

In [43]:
def euler_lagrange(lagr, qs, var):
    r"""
    Derive the Euler-Lagrange equations from a given Lagrangian.

    INPUT:

    - ``lagr`` -- symbolic expression representing the Lagrangian density
    - ``qs`` -- either a single symbolic function or a list/tuple of
      symbolic functions, representing the `q`'s; these functions must
      appear in ``lagr`` up to at most their first derivatives
    - ``var`` -- either a single variable, typically `t` (1-dimensional
      problem) or a list/tuple of symbolic variables

    OUTPUT:

    - list of Euler-Lagrange equations; if only one function is involved, the
      single Euler-Lagrannge equation is returned instead.

    """
    if not isinstance(qs, (list, tuple)):
        qs = [qs]
    if not isinstance(var, (list, tuple)):
        var = [var]
    n = len(qs)
    d = len(var)
    qv = [SR.var('qxxxx{}'.format(q)) for q in qs]
    dqv = [[SR.var('qxxxx{}_{}'.format(q, v)) for v in var] for q in qs]
    subs = {qs[i](*var): qv[i] for i in range(n)}
    subs_inv = {qv[i]: qs[i](*var) for i in range(n)}
    for i in range(n):
        subs.update({diff(qs[i](*var), var[j]): dqv[i][j]
                     for j in range(d)})
        subs_inv.update({dqv[i][j]: diff(qs[i](*var), var[j])
                         for j in range(d)})
    lg = lagr.substitute(subs)
    eqs = []
    for i in range(n):
        dLdq = diff(lg, qv[i]).simplify_full()
        dLdq = dLdq.substitute(subs_inv)
        ddL = 0
        for j in range(d):
            h =  diff(lg, dqv[i][j]).simplify_full()
            h = h.substitute(subs_inv)
            ddL += diff(h, var[j])
        eqs.append((dLdq - ddL).simplify_full() == 0)
    if n == 1:
        return eqs[0]
    return eqs

We compute the Euler-Lagrange equations at order $a^2$ for $\phi_1$ and $\psi_1$:

In [44]:
eqs = euler_lagrange(L_a2, [phi_1, psi_1], r)
eqs

[2*(2*(Mu0^2 - 1)*a^2*l^2*r^3 + (Mu0^2 - 1)*a^2*r)*diff(phi_1(r), r) + ((Mu0^2 - 1)*a^2*l^2*r^4 + (Mu0^2 - 1)*a^2*r^2 - 2*(Mu0^2 - 1)*a^2*m)*diff(phi_1(r), r, r) == 0,
 -2*(2*Mu0^2*a^2*l^2*n^2*r^3 + Mu0^2*a^2*n^2*r)*diff(psi_1(r), r) - (Mu0^2*a^2*l^2*n^2*r^4 + Mu0^2*a^2*n^2*r^2 - 2*Mu0^2*a^2*m*n^2)*diff(psi_1(r), r, r) == 0]

#### Solving the equation for $\phi_1$ (Eq. (4.8))

In [45]:
eq_phi1 = eqs[0]
eq_phi1

2*(2*(Mu0^2 - 1)*a^2*l^2*r^3 + (Mu0^2 - 1)*a^2*r)*diff(phi_1(r), r) + ((Mu0^2 - 1)*a^2*l^2*r^4 + (Mu0^2 - 1)*a^2*r^2 - 2*(Mu0^2 - 1)*a^2*m)*diff(phi_1(r), r, r) == 0

In [46]:
eq_phi1 = (eq_phi1/(a^2*(Mu0^2-1))).simplify_full()
eq_phi1

2*(2*l^2*r^3 + r)*diff(phi_1(r), r) + (l^2*r^4 + r^2 - 2*m)*diff(phi_1(r), r, r) == 0

In [47]:
phi1_sol(r) = desolve(eq_phi1, phi_1(r), ivar=r)
phi1_sol(r)

_K1*integrate(1/(l^2*r^4 + r^2 - 2*m), r) + _K2

We recover Eqs. (4.8) with $K_1 = \mathfrak{p}$ and $K_2=0$.

The symbolic constants $K_1$ and $K_2$ are actually denoted `_K1` and `_K2` by SageMath, as the `print` reveals:

In [48]:
print(phi1_sol(r))

_K1*integrate(1/(l^2*r^4 + r^2 - 2*m), r) + _K2


Hence we perform the substitutions with `SR.var('_K1')` and `SR.var('_K2')`:

In [49]:
pf = var("pf", latex_name=r"\mathfrak{p}")
phi1_sol(r) = phi1_sol(r).subs({SR.var('_K1'): pf, SR.var('_K2'): 0})
phi1_sol(r)

pf*integrate(1/(l^2*r^4 + r^2 - 2*m), r)

#### Solving the equation for $\psi_1$  (Eq. (4.8))

In [50]:
eq_psi1 = eqs[1]
eq_psi1

-2*(2*Mu0^2*a^2*l^2*n^2*r^3 + Mu0^2*a^2*n^2*r)*diff(psi_1(r), r) - (Mu0^2*a^2*l^2*n^2*r^4 + Mu0^2*a^2*n^2*r^2 - 2*Mu0^2*a^2*m*n^2)*diff(psi_1(r), r, r) == 0

In [51]:
eq_psi1 = (eq_psi1/(a^2*Mu0^2)).simplify_full()
eq_psi1

-2*(2*l^2*n^2*r^3 + n^2*r)*diff(psi_1(r), r) - (l^2*n^2*r^4 + n^2*r^2 - 2*m*n^2)*diff(psi_1(r), r, r) == 0

In [52]:
psi1_sol(r) = desolve(eq_psi1, psi_1(r), ivar=r)
psi1_sol(r)

_K1*integrate(1/(l^2*r^4 + r^2 - 2*m), r) + _K2

We recover Eq. (4.8) with $K_1 = \mathfrak{q}$ and $K_2=0$.

In [53]:
qf = var('qf', latex_name=r"\mathfrak{q}")
psi1_sol(r) = psi1_sol(r).subs({SR.var('_K1'): qf, SR.var('_K2'): 0})
psi1_sol(r)

qf*integrate(1/(l^2*r^4 + r^2 - 2*m), r)

### Nambu-Goto Lagrangian at fourth order in $a$

In [54]:
L_a4 = (sqrt(-detg_a4)).series(a, 5).truncate().simplify_full()

In [55]:
eqs = euler_lagrange(L_a4, [phi_1, psi_1, mu_1], r)

### The equation for $\mu_1$

In [56]:
eq_mu1 = eqs[2]
eq_mu1

-(4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4 - (4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n^4 + 3*((Mu0^3 - Mu0)*a^4*l^4*n^4 + 2*(Mu0^3 - Mu0)*a^4*l^4*n^3 - 2*(Mu0^3 - Mu0)*a^4*l^4*n - (Mu0^3 - Mu0)*a^4*l^4)*r^4 - 2*(4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n^3 + (4*(Mu0^3 - Mu0)*a^4*m^2*n^2 + ((Mu0^3 - Mu0)*a^4*l^4*n^2 + 2*(Mu0^3 - Mu0)*a^4*l^4*n + (Mu0^3 - Mu0)*a^4*l^4)*r^8 + 8*(Mu0^3 - Mu0)*a^4*m^2*n + 4*(Mu0^3 - Mu0)*a^4*m^2 + 2*((Mu0^3 - Mu0)*a^4*l^2*n^2 + 2*(Mu0^3 - Mu0)*a^4*l^2*n + (Mu0^3 - Mu0)*a^4*l^2)*r^6 - (4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4 + (4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n^2 + 2*(4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n)*r^4 - 4*((Mu0^3 - Mu0)*a^4*m*n^2 + 2*(Mu0^3 - Mu0)*a^4*m*n + (Mu0^3 - Mu0)*a^4*m)*r^2)*diff(phi_1(r), r)^2 - (4*(Mu0^3 - Mu0)*a^4*m^2*n^4 + 8*(Mu0^3 - Mu0)*a^4*m^2*n^3 + 4*(Mu0^3 - Mu0)*a^4*m^2*n^2 + ((Mu0^3 - Mu0)*a^4*l^4*n^4 + 2*(Mu0^3 - Mu0)*a^4*l^4*n^3 + (Mu0^3 - Mu0)*a^4*l^4*n^2)*r^8 + 2*((Mu0^3 - Mu0)*a^4*l^2*n^4 + 2*(Mu0^3 - Mu0)*a^4*l^2*n^3 + (Mu0^3 - Mu0)*a^4*l^2*n^2)*r^6 - ((4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n^4 + 2*(4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n^3 + (4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n^2)*r^4 - 4*((Mu0^3 - Mu0)*a^4*m*n^4 + 2*(Mu0^3 - Mu0)*a^4*m*n^3 + (Mu0^3 - Mu0)*a^4*m*n^2)*r^2)*diff(psi_1(r), r)^2 + 2*(4*(Mu0^3 - Mu0)*a^4*l^2*m - (Mu0^3 - Mu0)*a^4)*n - 2*(2*(a^4*l^4*n^4 + 4*a^4*l^4*n^3 + 6*a^4*l^4*n^2 + 4*a^4*l^4*n + a^4*l^4)*r^7 + 3*(a^4*l^2*n^4 + 4*a^4*l^2*n^3 + 6*a^4*l^2*n^2 + 4*a^4*l^2*n + a^4*l^2)*r^5 - (4*a^4*l^2*m + (4*a^4*l^2*m - a^4)*n^4 - a^4 + 4*(4*a^4*l^2*m - a^4)*n^3 + 6*(4*a^4*l^2*m - a^4)*n^2 + 4*(4*a^4*l^2*m - a^4)*n)*r^3 - 2*(a^4*m*n^4 + 4*a^4*m*n^3 + 6*a^4*m*n^2 + 4*a^4*m*n + a^4*m)*r)*diff(mu_1(r), r) - (4*a^4*m^2*n^4 + 16*a^4*m^2*n^3 + (a^4*l^4*n^4 + 4*a^4*l^4*n^3 + 6*a^4*l^4*n^2 + 4*a^4*l^4*n + a^4*l^4)*r^8 + 24*a^4*m^2*n^2 + 16*a^4*m^2*n + 2*(a^4*l^2*n^4 + 4*a^4*l^2*n^3 + 6*a^4*l^2*n^2 + 4*a^4*l^2*n + a^4*l^2)*r^6 + 4*a^4*m^2 - (4*a^4*l^2*m + (4*a^4*l^2*m - a^4)*n^4 - a^4 + 4*(4*a^4*l^2*m - a^4)*n^3 + 6*(4*a^4*l^2*m - a^4)*n^2 + 4*(4*a^4*l^2*m - a^4)*n)*r^4 - 4*(a^4*m*n^4 + 4*a^4*m*n^3 + 6*a^4*m*n^2 + 4*a^4*m*n + a^4*m)*r^2)*diff(mu_1(r), r, r))/((Mu0^2 - 1)*l^2*r^4 + (Mu0^2 - 1)*r^2 - 2*(Mu0^2 - 1)*m) == 0

In [57]:
eq_mu1.lhs().denominator().simplify_full()

(Mu0^2 - 1)*l^2*r^4 + (Mu0^2 - 1)*r^2 - 2*(Mu0^2 - 1)*m

In [58]:
eq_mu1 = eq_mu1.lhs().numerator().simplify_full() == 0
#eq_mu1

In [59]:
eq_mu1 = (eq_mu1/a^4).simplify_full()
eq_mu1

(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^4 - 3*((Mu0^3 - Mu0)*l^4*n^4 + 2*(Mu0^3 - Mu0)*l^4*n^3 - 2*(Mu0^3 - Mu0)*l^4*n - (Mu0^3 - Mu0)*l^4)*r^4 - 4*(Mu0^3 - Mu0)*l^2*m + 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^3 + Mu0^3 - (((Mu0^3 - Mu0)*l^4*n^2 + 2*(Mu0^3 - Mu0)*l^4*n + (Mu0^3 - Mu0)*l^4)*r^8 + 2*((Mu0^3 - Mu0)*l^2*n^2 + 2*(Mu0^3 - Mu0)*l^2*n + (Mu0^3 - Mu0)*l^2)*r^6 + 4*(Mu0^3 - Mu0)*m^2*n^2 - (4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + (4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^2 + 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n + Mu0)*r^4 + 8*(Mu0^3 - Mu0)*m^2*n + 4*(Mu0^3 - Mu0)*m^2 - 4*((Mu0^3 - Mu0)*m*n^2 + 2*(Mu0^3 - Mu0)*m*n + (Mu0^3 - Mu0)*m)*r^2)*diff(phi_1(r), r)^2 + (((Mu0^3 - Mu0)*l^4*n^4 + 2*(Mu0^3 - Mu0)*l^4*n^3 + (Mu0^3 - Mu0)*l^4*n^2)*r^8 + 4*(Mu0^3 - Mu0)*m^2*n^4 + 2*((Mu0^3 - Mu0)*l^2*n^4 + 2*(Mu0^3 - Mu0)*l^2*n^3 + (Mu0^3 - Mu0)*l^2*n^2)*r^6 + 8*(Mu0^3 - Mu0)*m^2*n^3 + 4*(Mu0^3 - Mu0)*m^2*n^2 - ((4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^4 + 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^3 + (4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^2)*r^4 - 4*((Mu0^3 - Mu0)*m*n^4 + 2*(Mu0^3 - Mu0)*m*n^3 + (Mu0^3 - Mu0)*m*n^2)*r^2)*diff(psi_1(r), r)^2 - 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n + 2*(2*(l^4*n^4 + 4*l^4*n^3 + 6*l^4*n^2 + 4*l^4*n + l^4)*r^7 + 3*(l^2*n^4 + 4*l^2*n^3 + 6*l^2*n^2 + 4*l^2*n + l^2)*r^5 - ((4*l^2*m - 1)*n^4 + 4*(4*l^2*m - 1)*n^3 + 4*l^2*m + 6*(4*l^2*m - 1)*n^2 + 4*(4*l^2*m - 1)*n - 1)*r^3 - 2*(m*n^4 + 4*m*n^3 + 6*m*n^2 + 4*m*n + m)*r)*diff(mu_1(r), r) + ((l^4*n^4 + 4*l^4*n^3 + 6*l^4*n^2 + 4*l^4*n + l^4)*r^8 + 2*(l^2*n^4 + 4*l^2*n^3 + 6*l^2*n^2 + 4*l^2*n + l^2)*r^6 + 4*m^2*n^4 + 16*m^2*n^3 - ((4*l^2*m - 1)*n^4 + 4*(4*l^2*m - 1)*n^3 + 4*l^2*m + 6*(4*l^2*m - 1)*n^2 + 4*(4*l^2*m - 1)*n - 1)*r^4 + 24*m^2*n^2 + 16*m^2*n - 4*(m*n^4 + 4*m*n^3 + 6*m*n^2 + 4*m*n + m)*r^2 + 4*m^2)*diff(mu_1(r), r, r) - Mu0 == 0

We plug the solutions obtained previously for $\phi_1(r)$ and $\psi_1(r)$ in this equation:

In [60]:
eq_mu1 = eq_mu1.substitute_function(phi_1, phi1_sol).substitute_function(psi_1, psi1_sol)
eq_mu1 = eq_mu1.simplify_full()
eq_mu1

(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^4 - 3*((Mu0^3 - Mu0)*l^4*n^4 + 2*(Mu0^3 - Mu0)*l^4*n^3 - 2*(Mu0^3 - Mu0)*l^4*n - (Mu0^3 - Mu0)*l^4)*r^4 - 4*(Mu0^3 - Mu0)*l^2*m + 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^3 + Mu0^3 - (Mu0^3 + (Mu0^3 - Mu0)*n^2 + 2*(Mu0^3 - Mu0)*n - Mu0)*pf^2 + ((Mu0^3 - Mu0)*n^4 + 2*(Mu0^3 - Mu0)*n^3 + (Mu0^3 - Mu0)*n^2)*qf^2 - 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n + 2*(2*(l^4*n^4 + 4*l^4*n^3 + 6*l^4*n^2 + 4*l^4*n + l^4)*r^7 + 3*(l^2*n^4 + 4*l^2*n^3 + 6*l^2*n^2 + 4*l^2*n + l^2)*r^5 - ((4*l^2*m - 1)*n^4 + 4*(4*l^2*m - 1)*n^3 + 4*l^2*m + 6*(4*l^2*m - 1)*n^2 + 4*(4*l^2*m - 1)*n - 1)*r^3 - 2*(m*n^4 + 4*m*n^3 + 6*m*n^2 + 4*m*n + m)*r)*diff(mu_1(r), r) + ((l^4*n^4 + 4*l^4*n^3 + 6*l^4*n^2 + 4*l^4*n + l^4)*r^8 + 2*(l^2*n^4 + 4*l^2*n^3 + 6*l^2*n^2 + 4*l^2*n + l^2)*r^6 + 4*m^2*n^4 + 16*m^2*n^3 - ((4*l^2*m - 1)*n^4 + 4*(4*l^2*m - 1)*n^3 + 4*l^2*m + 6*(4*l^2*m - 1)*n^2 + 4*(4*l^2*m - 1)*n - 1)*r^4 + 24*m^2*n^2 + 16*m^2*n - 4*(m*n^4 + 4*m*n^3 + 6*m*n^2 + 4*m*n + m)*r^2 + 4*m^2)*diff(mu_1(r), r, r) - Mu0 == 0

### Check of Eq. (4.9)

In [61]:
lhs = eq_mu1.lhs()
lhs = lhs.simplify_full()
lhs

(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^4 - 3*((Mu0^3 - Mu0)*l^4*n^4 + 2*(Mu0^3 - Mu0)*l^4*n^3 - 2*(Mu0^3 - Mu0)*l^4*n - (Mu0^3 - Mu0)*l^4)*r^4 - 4*(Mu0^3 - Mu0)*l^2*m + 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^3 + Mu0^3 - (Mu0^3 + (Mu0^3 - Mu0)*n^2 + 2*(Mu0^3 - Mu0)*n - Mu0)*pf^2 + ((Mu0^3 - Mu0)*n^4 + 2*(Mu0^3 - Mu0)*n^3 + (Mu0^3 - Mu0)*n^2)*qf^2 - 2*(4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n + 2*(2*(l^4*n^4 + 4*l^4*n^3 + 6*l^4*n^2 + 4*l^4*n + l^4)*r^7 + 3*(l^2*n^4 + 4*l^2*n^3 + 6*l^2*n^2 + 4*l^2*n + l^2)*r^5 - ((4*l^2*m - 1)*n^4 + 4*(4*l^2*m - 1)*n^3 + 4*l^2*m + 6*(4*l^2*m - 1)*n^2 + 4*(4*l^2*m - 1)*n - 1)*r^3 - 2*(m*n^4 + 4*m*n^3 + 6*m*n^2 + 4*m*n + m)*r)*diff(mu_1(r), r) + ((l^4*n^4 + 4*l^4*n^3 + 6*l^4*n^2 + 4*l^4*n + l^4)*r^8 + 2*(l^2*n^4 + 4*l^2*n^3 + 6*l^2*n^2 + 4*l^2*n + l^2)*r^6 + 4*m^2*n^4 + 16*m^2*n^3 - ((4*l^2*m - 1)*n^4 + 4*(4*l^2*m - 1)*n^3 + 4*l^2*m + 6*(4*l^2*m - 1)*n^2 + 4*(4*l^2*m - 1)*n - 1)*r^4 + 24*m^2*n^2 + 16*m^2*n - 4*(m*n^4 + 4*m*n^3 + 6*m*n^2 + 4*m*n + m)*r^2 + 4*m^2)*diff(mu_1(r), r, r) - Mu0

In [62]:
s = lhs.coefficient(diff(mu_1(r), r, 2))  # coefficient of mu_1''
s.factor()

(l^2*r^4 + r^2 - 2*m)^2*(n + 1)^4

In [63]:
s1 = (lhs/s - diff(mu_1(r), r, 2)).simplify_full()
s1

((Mu0^3 - Mu0)*n^2*qf^2 - 3*((Mu0^3 - Mu0)*l^4*n^2 - (Mu0^3 - Mu0)*l^4)*r^4 - 4*(Mu0^3 - Mu0)*l^2*m + Mu0^3 + (4*(Mu0^3 - Mu0)*l^2*m - Mu0^3 + Mu0)*n^2 - (Mu0^3 - Mu0)*pf^2 + 2*(2*(l^4*n^2 + 2*l^4*n + l^4)*r^7 + 3*(l^2*n^2 + 2*l^2*n + l^2)*r^5 - (4*l^2*m + (4*l^2*m - 1)*n^2 + 2*(4*l^2*m - 1)*n - 1)*r^3 - 2*(m*n^2 + 2*m*n + m)*r)*diff(mu_1(r), r) - Mu0)/((l^4*n^2 + 2*l^4*n + l^4)*r^8 + 2*(l^2*n^2 + 2*l^2*n + l^2)*r^6 - (4*l^2*m + (4*l^2*m - 1)*n^2 + 2*(4*l^2*m - 1)*n - 1)*r^4 + 4*m^2*n^2 + 8*m^2*n - 4*(m*n^2 + 2*m*n + m)*r^2 + 4*m^2)

In [64]:
b1 = s1.coefficient(diff(mu_1(r), r)).factor()
b1

2*(2*l^2*r^2 + 1)*r/(l^2*r^4 + r^2 - 2*m)

In [65]:
b2 = (s1 - b1*diff(mu_1(r), r)).simplify_full().factor()
b2

-(3*l^4*n^2*r^4 - 3*l^4*r^4 - 4*l^2*m*n^2 - n^2*qf^2 + 4*l^2*m + n^2 + pf^2 - 1)*(Mu0 + 1)*(Mu0 - 1)*Mu0/((l^2*r^4 + r^2 - 2*m)^2*(n + 1)^2)

The equation for $\mu_1$ is thus:

In [66]:
eq_mu1 = diff(mu_1(r), r, 2) + b1*diff(mu_1(r), r) + b2 == 0
eq_mu1

2*(2*l^2*r^2 + 1)*r*diff(mu_1(r), r)/(l^2*r^4 + r^2 - 2*m) - (3*l^4*n^2*r^4 - 3*l^4*r^4 - 4*l^2*m*n^2 - n^2*qf^2 + 4*l^2*m + n^2 + pf^2 - 1)*(Mu0 + 1)*(Mu0 - 1)*Mu0/((l^2*r^4 + r^2 - 2*m)^2*(n + 1)^2) + diff(mu_1(r), r, r) == 0

Let us define
$$ \Theta_2 := 2 \Theta_0$$

In [67]:
Th2 = var('Th2', latex_name=r'\Theta_2', 
          domain='real')

Given that 
$$ \mu_1(r) = - \sin\Theta_0 \; \theta_1(r) = - \sqrt{1-\mu_0^2}  \; \theta_1(r)$$
and
$$\sin2\Theta_0 = 2\mu_0\sqrt{1-\mu_0^2},$$
we get the equation for $\Upsilon := \theta_1' = - \frac{\mu_1'}{\sqrt{1 - \mu_0}}$:

In [68]:
Y = function('Y', latex_name=r'\Upsilon')
eq_Y = diff(Y(r), r) + b1*Y(r) \
       - (b2/(2*(1-Mu0^2)*Mu0)*sin(Th2)).factor() == 0
eq_Y

2*(2*l^2*r^2 + 1)*r*Y(r)/(l^2*r^4 + r^2 - 2*m) - 1/2*(3*l^4*n^2*r^4 - 3*l^4*r^4 - 4*l^2*m*n^2 - n^2*qf^2 + 4*l^2*m + n^2 + pf^2 - 1)*sin(Th2)/((l^2*r^4 + r^2 - 2*m)^2*(n + 1)^2) + diff(Y(r), r) == 0

This agrees with Eq. (4.9) of the paper.

### Solving the equation for $\Upsilon := \theta_1'$

We use the function `desolve` to solve the differential equation for $\Upsilon$:

In [69]:
Y_sol(r) = desolve(eq_Y, Y(r), ivar=r)

The solution involves an integral that SageMath is not capable to evaluate with the default integrator. Trying to display `Y_sol` would make SageMath hang. Instead, we print `Y_sol` to get the unvaluated form of the integral, in order to compute it by means of FriCAS:

In [70]:
print(Y_sol(r))

1/2*(2*_C + 3*(l^2*n*sin(Th2) - l^2*sin(Th2))*r/(n + 1) - integrate((n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 + 3*(l^2*n^2 - l^2)*r^2 - pf^2 + 1)/(l^2*r^4 + r^2 - 2*m), r)*sin(Th2)/(n^2 + 2*n + 1))/(l^2*r^4 + r^2 - 2*m)


The solution involves some constant, denoted `_C` by SageMath. We rename it `C_1` and 
rewrite the above solution as

In [71]:
C_1 = var('C_1')
Integ(r) = function('Integ')(r)
Y_sol0(r) = 1/2*(2*C_1 + 3*(l^2*n*sin(Th2) - l^2*sin(Th2))*r/(n + 1) \
                 - Integ(r)*sin(Th2)/(n^2 + 2*n + 1))/(l^2*r^4 + r^2 - 2*m)
Y_sol0(r)

1/2*(2*C_1 + 3*(l^2*n*sin(Th2) - l^2*sin(Th2))*r/(n + 1) - Integ(r)*sin(Th2)/(n^2 + 2*n + 1))/(l^2*r^4 + r^2 - 2*m)

`Integ(r)` represents the integral $I(r)$, whose integrand, $F(r)$ say, is read from the
output of `print(Y_sol(r))`:

In [72]:
F(r) = (n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 + 3*(l^2*n^2 - l^2)*r^2 - pf^2 + 1) \
       /(l^2*r^4 + r^2 - 2*m)
F(r)

(n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 + 3*(l^2*n^2 - l^2)*r^2 - pf^2 + 1)/(l^2*r^4 + r^2 - 2*m)

We split the integral in two parts:
$$ I(r) = F_1 \; s_1(r) + F_2 \; s_2(r)$$
with 
$$ s_1(r) := \int^r \frac{\bar{r}^2}{\ell^2 \bar{r}^4 + \bar{r}^2 - 2m} \, \mathrm{d}\bar{r}, \qquad  s_2(r) := \int^r \frac{\mathrm{d}\bar{r}}{\ell^2 \bar{r}^4 + \bar{r}^2 - 2m} $$
and

In [73]:
F1 = 3*(l^2*n^2 - l^2)
F1

3*l^2*n^2 - 3*l^2

In [74]:
F2 = n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 - pf^2 + 1
F2

n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 - pf^2 + 1

Check:

In [75]:
bool(F(r) == F1*r^2/(l^2*r^4 + r^2 - 2*m) + F2/(l^2*r^4 + r^2 - 2*m))

True

Let us evaluate $s_1(r)$ by means of FriCAS:

In [76]:
s1 = integrate(r^2/(l^2*r^4 + r^2 - 2*m), r, algorithm='fricas')
s1

1/2*sqrt(1/2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))*log(sqrt(1/2)*(8*l^4*m + l^2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r) - 1/2*sqrt(1/2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))*log(-sqrt(1/2)*(8*l^4*m + l^2)*sqrt(-((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) + 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r) - 1/2*sqrt(1/2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))*log(sqrt(1/2)*(8*l^4*m + l^2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r) + 1/2*sqrt(1/2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))*log(-sqrt(1/2)*(8*l^4*m + l^2)*sqrt(((8*l^4*m + l^2)/sqrt(8*l^6*m + l^4) - 1)/(8*l^4*m + l^2))/sqrt(8*l^6*m + l^4) + r)

In [77]:
s1 = s1.canonicalize_radical().simplify_log()
s1

1/4*(sqrt(2)*sqrt(8*l^2*m - sqrt(8*l^2*m + 1) + 1)*log((sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r - sqrt(8*l^2*m - sqrt(8*l^2*m + 1) + 1))/(sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r + sqrt(8*l^2*m - sqrt(8*l^2*m + 1) + 1))) + sqrt(2)*sqrt(-8*l^2*m - sqrt(8*l^2*m + 1) - 1)*log((sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r + sqrt(-8*l^2*m - sqrt(8*l^2*m + 1) - 1))/(sqrt(2)*(8*l^2*m + 1)^(1/4)*l*r - sqrt(-8*l^2*m - sqrt(8*l^2*m + 1) - 1))))/((8*l^2*m + 1)^(3/4)*l)

Check:

In [78]:
diff(s1, r).simplify_full()

r^2/(l^2*r^4 + r^2 - 2*m)

Similarly, we evaluate $s_2(r)$ by means of FriCAS:

In [79]:
s2 = integrate(1/(l^2*r^4 + r^2 - 2*m), r, algorithm='fricas')
s2

-1/4*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))*log(2*l^2*r + 1/2*(8*l^2*m - (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))) + 1/4*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))*log(2*l^2*r - 1/2*(8*l^2*m - (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)/(8*l^2*m^2 + m))) - 1/4*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m))*log(2*l^2*r + 1/2*(8*l^2*m + (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m))) + 1/4*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m))*log(2*l^2*r - 1/2*(8*l^2*m + (8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) + 1)*sqrt(-((8*l^2*m^2 + m)/sqrt(8*l^2*m^3 + m^2) - 1)/(8*l^2*m^2 + m)))

In [80]:
s2 = s2.canonicalize_radical().simplify_log()
s2

1/4*(sqrt(-8*l^2*m + sqrt(8*l^2*m + 1) - 1)*log((4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r - sqrt(-8*l^2*m + sqrt(8*l^2*m + 1) - 1)*(sqrt(8*l^2*m + 1) + 1))/(4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r + sqrt(-8*l^2*m + sqrt(8*l^2*m + 1) - 1)*(sqrt(8*l^2*m + 1) + 1))) + sqrt(8*l^2*m + sqrt(8*l^2*m + 1) + 1)*log((4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r - sqrt(8*l^2*m + sqrt(8*l^2*m + 1) + 1)*(sqrt(8*l^2*m + 1) - 1))/(4*(8*l^2*m + 1)^(1/4)*l^2*sqrt(m)*r + sqrt(8*l^2*m + sqrt(8*l^2*m + 1) + 1)*(sqrt(8*l^2*m + 1) - 1))))/((8*l^2*m + 1)^(3/4)*sqrt(m))

Check:

In [81]:
diff(s2, r).simplify_full()

1/(l^2*r^4 + r^2 - 2*m)

In the above expressions for $s_1(r)$ and $s_2(r)$ there appears $\sqrt{1 + 8 \ell^2 m}$,
which can be rewritten
$$
    \sqrt{1 + 8 \ell^2 m} = 2 \ell^2 r_H^2 + 1 
$$
where $r_H$ is the positive root of $\ell^2 r_H^4 + r_H^2 - 2m = 0$. More precisely, we perform the following substitution:
$$
   m = \frac{1}{2} r_H^2 (\ell^2 r_H^2 + 1)
$$

In [82]:
rH = var('rH', latex_name=r'r_H', domain='real')
assume(rH > 0)
m_rH = rH^2*(l^2*rH^2 + 1)/2
s1 = s1.subs({m: m_rH}).canonicalize_radical().simplify_log()
s1

-1/2*(l*rH*log((r + rH)/(r - rH)) + I*sqrt(l^2*rH^2 + 1)*log((l*r - I*sqrt(l^2*rH^2 + 1))/(l*r + I*sqrt(l^2*rH^2 + 1))))/(2*l^3*rH^2 + l)

In the second $\log$, we recognize the $\mathrm{arccot}$ function, via the identity
$$
    \mathrm{arccot}\,  x =  \frac{i}{2} \ln\left( \frac{x - i}{x + i} \right) . 
$$
Given that $\mathrm{arccot}\,  x = \pi/2 - \mathrm{arctan}\, x$, we use this identity as
$$
i \ln\left( \frac{x - i}{x + i} \right) = - 2 \, \mathrm{arctan}(x) + \pi
$$

Thus, we perform the following substitution, disregarding the additive constant $\pi$:

In [83]:
s1 = s1.subs({I*sqrt(l^2*rH^2 + 1)*log((l*r - I*sqrt(l^2*rH^2 + 1))/(l*r + I*sqrt(l^2*rH^2 + 1))):
              -2*sqrt(l^2*rH^2 + 1)*atan(l*r/sqrt(l^2*rH^2 + 1))})
s1

-1/2*(l*rH*log((r + rH)/(r - rH)) - 2*sqrt(l^2*rH^2 + 1)*arctan(l*r/sqrt(l^2*rH^2 + 1)))/(2*l^3*rH^2 + l)

Let us check that we have indeed a primitive of $r\mapsto \frac{r^2}{\ell^2 r^4 + r^2 - 2m}$:

In [84]:
Ds1 = diff(s1, r).simplify_full()
Ds1

r^2/(l^2*r^4 - l^2*rH^4 + r^2 - rH^2)

In [85]:
rH_m = sqrt(sqrt(1 + 8*l^2*m) - 1)/(sqrt(2)*l)
Ds1.subs({rH: rH_m}).simplify_full()

r^2/(l^2*r^4 + r^2 - 2*m)

Similarly, let us express $s_2$ in terms of $r_H$:

In [86]:
s2 = s2.subs({m: m_rH}).canonicalize_radical().simplify_log()
s2

1/2*(I*l*rH*log((-I*l^2*rH^2 + sqrt(l^2*rH^2 + 1)*l*r - I)/(I*l^2*rH^2 + sqrt(l^2*rH^2 + 1)*l*r + I)) + sqrt(l^2*rH^2 + 1)*log((r - rH)/(r + rH)))/((2*l^2*rH^3 + rH)*sqrt(l^2*rH^2 + 1))

Again, we use the identity
$$
i \ln\left( \frac{x - i}{x + i} \right) = - 2 \, \mathrm{arctan}(x) + \pi
$$
to rewrite $s_2$ as

In [87]:
s2 = s2.subs({I*l*rH*log((-I*l^2*rH^2 + sqrt(l^2*rH^2 + 1)*l*r - I)/(I*l^2*rH^2 + sqrt(l^2*rH^2 + 1)*l*r + I)):
             -2*l*rH*atan(l*r/sqrt(l^2*rH^2 + 1))})
s2

-1/2*(2*l*rH*arctan(l*r/sqrt(l^2*rH^2 + 1)) - sqrt(l^2*rH^2 + 1)*log((r - rH)/(r + rH)))/((2*l^2*rH^3 + rH)*sqrt(l^2*rH^2 + 1))

Let us also replace $\ln\left(\frac{r - r_H}{r + r_H}\right)$ by $-\ln\left(\frac{r + r_H}{r - r_H}\right)$
in order to have the same log term as in $s_1(r)$:

In [88]:
s2 = s2.subs({log((r - rH)/(r + rH)): - log((r + rH)/(r - rH))})
s2

-1/2*(2*l*rH*arctan(l*r/sqrt(l^2*rH^2 + 1)) + sqrt(l^2*rH^2 + 1)*log((r + rH)/(r - rH)))/((2*l^2*rH^3 + rH)*sqrt(l^2*rH^2 + 1))

Let us check that we have indeed a primitive of $r\mapsto \frac{1}{\ell^2 r^4 + r^2 - 2m}$:

In [89]:
Ds2 = diff(s2, r).simplify_full()
Ds2

1/(l^2*r^4 - l^2*rH^4 + r^2 - rH^2)

In [90]:
Ds2.subs({rH: rH_m}).simplify_full()

1/(l^2*r^4 + r^2 - 2*m)

The full integral is thus

In [91]:
Integ0 = (F1*s1 + F2*s2).simplify_full()
Integ0

-1/2*((n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 + 3*(l^2*n^2 - l^2)*rH^2 - pf^2 + 1)*sqrt(l^2*rH^2 + 1)*log((r + rH)/(r - rH)) - 2*(3*(l^3*n^2 - l^3)*rH^3 - (l*n^2*qf^2 + 2*l^3*m - 2*(l^3*m + 2*l)*n^2 - l*pf^2 + 4*l)*rH)*arctan(l*r/sqrt(l^2*rH^2 + 1)))/((2*l^2*rH^3 + rH)*sqrt(l^2*rH^2 + 1))

so that the solution is

In [92]:
Y_sol(r) = Y_sol0(r).subs({Integ(r): Integ0}).simplify_full()
Y_sol(r)

1/4*(2*(3*(l^3*n^2*sin(Th2) - l^3*sin(Th2))*rH^3 - (l*n^2*qf^2*sin(Th2) + 2*l^3*m*sin(Th2) - l*pf^2*sin(Th2) - 2*(l^3*m*sin(Th2) + 2*l*sin(Th2))*n^2 + 4*l*sin(Th2))*rH)*arctan(l*r/sqrt(l^2*rH^2 + 1)) - sqrt(l^2*rH^2 + 1)*(4*(2*C_1*l^2*n^2 + 4*C_1*l^2*n + 2*C_1*l^2 + 3*(l^4*n^2*sin(Th2) - l^4*sin(Th2))*r)*rH^3 + 2*(2*C_1*n^2 + 4*C_1*n + 3*(l^2*n^2*sin(Th2) - l^2*sin(Th2))*r + 2*C_1)*rH + (n^2*qf^2*sin(Th2) + 2*l^2*m*sin(Th2) - (2*l^2*m*sin(Th2) + sin(Th2))*n^2 + 3*(l^2*n^2*sin(Th2) - l^2*sin(Th2))*rH^2 - pf^2*sin(Th2) + sin(Th2))*log((r + rH)/(r - rH))))/(sqrt(l^2*rH^2 + 1)*(2*(2*l^2*m*n^2 - (l^4*n^2 + 2*l^4*n + l^4)*r^4 + 4*l^2*m*n + 2*l^2*m - (l^2*n^2 + 2*l^2*n + l^2)*r^2)*rH^3 - ((l^2*n^2 + 2*l^2*n + l^2)*r^4 - 2*m*n^2 + (n^2 + 2*n + 1)*r^2 - 4*m*n - 2*m)*rH))

In [93]:
Y_sol(r).numerator().simplify_full()

-2*(3*(l^3*n^2*sin(Th2) - l^3*sin(Th2))*rH^3 - (l*n^2*qf^2*sin(Th2) + 2*l^3*m*sin(Th2) - l*pf^2*sin(Th2) - 2*(l^3*m*sin(Th2) + 2*l*sin(Th2))*n^2 + 4*l*sin(Th2))*rH)*arctan(l*r/sqrt(l^2*rH^2 + 1)) + sqrt(l^2*rH^2 + 1)*(4*(2*C_1*l^2*n^2 + 4*C_1*l^2*n + 2*C_1*l^2 + 3*(l^4*n^2*sin(Th2) - l^4*sin(Th2))*r)*rH^3 + 2*(2*C_1*n^2 + 4*C_1*n + 3*(l^2*n^2*sin(Th2) - l^2*sin(Th2))*r + 2*C_1)*rH + (n^2*qf^2*sin(Th2) + 2*l^2*m*sin(Th2) - (2*l^2*m*sin(Th2) + sin(Th2))*n^2 + 3*(l^2*n^2*sin(Th2) - l^2*sin(Th2))*rH^2 - pf^2*sin(Th2) + sin(Th2))*log((r + rH)/(r - rH)))

In [94]:
Y_sol(r).denominator().factor()

4*(l^2*r^4 + r^2 - 2*m)*(2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)*(n + 1)^2*rH

Let us check that `Y_sol` is indeed a solution of the differential equation for $\Upsilon$:

In [95]:
eq_Y.substitute_function(Y, Y_sol).subs({rH: rH_m}).simplify_full()

0 == 0

In [96]:
print(Y_sol(r))

1/4*(2*(3*(l^3*n^2*sin(Th2) - l^3*sin(Th2))*rH^3 - (l*n^2*qf^2*sin(Th2) + 2*l^3*m*sin(Th2) - l*pf^2*sin(Th2) - 2*(l^3*m*sin(Th2) + 2*l*sin(Th2))*n^2 + 4*l*sin(Th2))*rH)*arctan(l*r/sqrt(l^2*rH^2 + 1)) - sqrt(l^2*rH^2 + 1)*(4*(2*C_1*l^2*n^2 + 4*C_1*l^2*n + 2*C_1*l^2 + 3*(l^4*n^2*sin(Th2) - l^4*sin(Th2))*r)*rH^3 + 2*(2*C_1*n^2 + 4*C_1*n + 3*(l^2*n^2*sin(Th2) - l^2*sin(Th2))*r + 2*C_1)*rH + (n^2*qf^2*sin(Th2) + 2*l^2*m*sin(Th2) - (2*l^2*m*sin(Th2) + sin(Th2))*n^2 + 3*(l^2*n^2*sin(Th2) - l^2*sin(Th2))*rH^2 - pf^2*sin(Th2) + sin(Th2))*log((r + rH)/(r - rH))))/(sqrt(l^2*rH^2 + 1)*(2*(2*l^2*m*n^2 - (l^4*n^2 + 2*l^4*n + l^4)*r^4 + 4*l^2*m*n + 2*l^2*m - (l^2*n^2 + 2*l^2*n + l^2)*r^2)*rH^3 - ((l^2*n^2 + 2*l^2*n + l^2)*r^4 - 2*m*n^2 + (n^2 + 2*n + 1)*r^2 - 4*m*n - 2*m)*rH))


### Check of Eq. (4.10) (expression of $\theta'_1 = \Upsilon$)

The term involving the constant $C_1$ agrees with that of Eq. (4.10):

In [97]:
s = Y_sol(r).coefficient(C_1).simplify_full()
s

1/(l^2*r^4 + r^2 - 2*m)

In [98]:
fr4 = l^2*r^4 + r^2 - 2*m
bool(s == 1/fr4)

True

Let us remove it from $\Upsilon$ and divide the result by $\sin(2\Theta_0)$:

In [99]:
Y1 = ((Y_sol(r) - s*C_1)/sin(Th2)).simplify_full()
Y1

1/4*(2*(3*(l^3*n^2 - l^3)*rH^3 - (l*n^2*qf^2 + 2*l^3*m - 2*(l^3*m + 2*l)*n^2 - l*pf^2 + 4*l)*rH)*arctan(l*r/sqrt(l^2*rH^2 + 1)) - (12*(l^4*n^2 - l^4)*r*rH^3 + 6*(l^2*n^2 - l^2)*r*rH + (n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 + 3*(l^2*n^2 - l^2)*rH^2 - pf^2 + 1)*log((r + rH)/(r - rH)))*sqrt(l^2*rH^2 + 1))/(sqrt(l^2*rH^2 + 1)*(2*(2*l^2*m*n^2 - (l^4*n^2 + 2*l^4*n + l^4)*r^4 + 4*l^2*m*n + 2*l^2*m - (l^2*n^2 + 2*l^2*n + l^2)*r^2)*rH^3 - ((l^2*n^2 + 2*l^2*n + l^2)*r^4 - 2*m*n^2 + (n^2 + 2*n + 1)*r^2 - 4*m*n - 2*m)*rH))

The coefficient of the arctan term is

In [100]:
s = Y1.coefficient(arctan(l*r/sqrt(l^2*rH^2 + 1))).simplify_full().factor()
s

-1/2*(3*l^2*n^2*rH^2 + 2*l^2*m*n^2 - n^2*qf^2 - 3*l^2*rH^2 - 2*l^2*m + 4*n^2 + pf^2 - 4)*l/((l^2*r^4 + r^2 - 2*m)*(2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)*(n + 1)^2)

The numerator of this term agrees with Eq. (4.10):

In [101]:
s.numerator().subs({m: m_rH}).factor()

-(l^4*n^2*rH^4 - l^4*rH^4 + 4*l^2*n^2*rH^2 - n^2*qf^2 - 4*l^2*rH^2 + 4*n^2 + pf^2 - 4)*l

In [102]:
bool(s.numerator().subs({m: m_rH}) 
     == l*((1 - n^2)*(l^2*rH^2 + 2)^2 - pf^2 + n^2*qf^2))

True

The denominator agrees with Eq. (4.10) as well:

In [103]:
s.denominator()

2*(l^2*r^4 + r^2 - 2*m)*(2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)*(n + 1)^2

Let us remove the arctan term from $\Upsilon$:

In [104]:
Y2 = (Y1 - s*arctan(l*r/sqrt(l^2*rH^2 + 1))).simplify_full()
Y2

-1/4*(12*(l^4*n^2 - l^4)*r*rH^3 + 6*(l^2*n^2 - l^2)*r*rH + (n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 + 3*(l^2*n^2 - l^2)*rH^2 - pf^2 + 1)*log((r + rH)/(r - rH)))/(2*(2*l^2*m*n^2 - (l^4*n^2 + 2*l^4*n + l^4)*r^4 + 4*l^2*m*n + 2*l^2*m - (l^2*n^2 + 2*l^2*n + l^2)*r^2)*rH^3 - ((l^2*n^2 + 2*l^2*n + l^2)*r^4 - 2*m*n^2 + (n^2 + 2*n + 1)*r^2 - 4*m*n - 2*m)*rH)

In [105]:
Y2.numerator().simplify_full()

12*(l^4*n^2 - l^4)*r*rH^3 + 6*(l^2*n^2 - l^2)*r*rH + (n^2*qf^2 + 2*l^2*m - (2*l^2*m + 1)*n^2 + 3*(l^2*n^2 - l^2)*rH^2 - pf^2 + 1)*log((r + rH)/(r - rH))

In [106]:
Y2.denominator().factor()

4*(l^2*r^4 + r^2 - 2*m)*(2*l^2*rH^2 + 1)*(n + 1)^2*rH

The coefficient of the log term is

In [107]:
s = Y2.coefficient(log((r + rH)/(r - rH))).simplify_full().factor()
s

1/4*(3*l^2*n^2*rH^2 - 2*l^2*m*n^2 + n^2*qf^2 - 3*l^2*rH^2 + 2*l^2*m - n^2 - pf^2 + 1)/((l^2*r^4 + r^2 - 2*m)*(2*l^2*rH^2 + 1)*(n + 1)^2*rH)

In [108]:
s.numerator().subs({m: m_rH}).factor()

-l^4*n^2*rH^4 + l^4*rH^4 + 2*l^2*n^2*rH^2 + n^2*qf^2 - 2*l^2*rH^2 - n^2 - pf^2 + 1

Check against Eq. (4.10):

In [109]:
bool(s.numerator().subs({m: m_rH}) == (1 - n^2)*(l^2*rH^2 - 1)^2 - pf^2 + n^2*qf^2)

True

In [110]:
s.denominator()

4*(l^2*r^4 + r^2 - 2*m)*(2*l^2*rH^2 + 1)*(n + 1)^2*rH

Given that 
$$ \mathrm{artanh}\, x = \frac{1}{2} \ln\left( \frac{1 + x}{1 - x} \right) $$
we have
$$
   \ln \left( \frac{x + 1}{x - 1} \right) = 2\, \mathrm{artanh}\left(\frac{1}{x}\right)
$$

Hence the term in $\ln\left(\frac{r + r_H}{r - r_H}\right)$ agrees with the corresponding term in Eq. (4.10).

Finally, the last term in $\Upsilon$ is

In [111]:
Y3 = (Y2 - s*log((r + rH)/(r - rH))).simplify_full()
Y3.factor()

3/2*l^2*(n - 1)*r/((l^2*r^4 + r^2 - 2*m)*(n + 1))

This term agrees with Eq. (4.10), given the simplification 
$\frac{1 - n^2}{(1 + n)^2} = -\frac{n - 1}{n + 1}$.

**Conclusion:** we have full agreement with Eq. (4.10).

### Conjugate momenta

In [112]:
def conjugate_momenta(lagr, qs, var):
    r"""
    Compute the conjugate momenta from a given Lagrangian.

    INPUT:

    - ``lagr`` -- symbolic expression representing the Lagrangian density
    - ``qs`` -- either a single symbolic function or a list/tuple of
      symbolic functions, representing the `q`'s; these functions must
      appear in ``lagr`` up to at most their first derivatives
    - ``var`` -- either a single variable, typically `t` (1-dimensional
      problem) or a list/tuple of symbolic variables; in the latter case the
      time coordinate must the first one

    OUTPUT:

    - list of conjugate momenta; if only one function is involved, the
      single conjugate momentum is returned instead.

    """
    if not isinstance(qs, (list, tuple)):
        qs = [qs]
    if not isinstance(var, (list, tuple)):
        var = [var]
    n = len(qs)
    d = len(var)
    dqvt = [SR.var('qxxxx{}_t'.format(q)) for q in qs]
    subs = {diff(qs[i](*var), var[0]): dqvt[i] for i in range(n)}
    subs_inv = {dqvt[i]: diff(qs[i](*var), var[0]) for i in range(n)}
    lg = lagr.substitute(subs)
    ps = [diff(lg, dotq).simplify_full().substitute(subs_inv) for dotq in dqvt]
    if n == 1:
        return ps[0]
    return ps

In [113]:
pis = conjugate_momenta(L_a2, [phi_1, psi_1], r)
pis

[-(Mu0^2 - 1)*a^2*l^2*r^4*diff(phi_1(r), r) - (Mu0^2 - 1)*a^2*r^2*diff(phi_1(r), r) + 2*(Mu0^2 - 1)*a^2*m*diff(phi_1(r), r),
 Mu0^2*a^2*l^2*n^2*r^4*diff(psi_1(r), r) + Mu0^2*a^2*n^2*r^2*diff(psi_1(r), r) - 2*Mu0^2*a^2*m*n^2*diff(psi_1(r), r)]

### Check of Eq. (4.15):

In [114]:
pi_phi_r = (pis[0]/a).substitute_function(phi_1, phi1_sol).simplify_full()
pi_phi_r

-(Mu0^2 - 1)*a*pf

In [115]:
pi_psi_r = (pis[1]/a).substitute_function(psi_1, psi1_sol).simplify_full()
pi_psi_r

Mu0^2*a*n^2*qf

### Check of Eq. (4.14):

We start from $\pi^r_\theta$ as given by Eq. (4.13):

In [116]:
pi_theta = (fr4*(a + b)^2*Y_sol(r)).simplify_full()
pi_theta 

-1/4*(2*(3*(a^2*l^3*n^2*sin(Th2) - a^2*l^3*sin(Th2))*rH^3 - (a^2*l*n^2*qf^2*sin(Th2) + 2*a^2*l^3*m*sin(Th2) - a^2*l*pf^2*sin(Th2) + 4*a^2*l*sin(Th2) - 2*(a^2*l^3*m*sin(Th2) + 2*a^2*l*sin(Th2))*n^2)*rH)*arctan(l*r/sqrt(l^2*rH^2 + 1)) - sqrt(l^2*rH^2 + 1)*(4*(2*C_1*a^2*l^2*n^2 + 4*C_1*a^2*l^2*n + 2*C_1*a^2*l^2 + 3*(a^2*l^4*n^2*sin(Th2) - a^2*l^4*sin(Th2))*r)*rH^3 + 2*(2*C_1*a^2*n^2 + 4*C_1*a^2*n + 2*C_1*a^2 + 3*(a^2*l^2*n^2*sin(Th2) - a^2*l^2*sin(Th2))*r)*rH + (a^2*n^2*qf^2*sin(Th2) + 2*a^2*l^2*m*sin(Th2) - a^2*pf^2*sin(Th2) - (2*a^2*l^2*m*sin(Th2) + a^2*sin(Th2))*n^2 + 3*(a^2*l^2*n^2*sin(Th2) - a^2*l^2*sin(Th2))*rH^2 + a^2*sin(Th2))*log((r + rH)/(r - rH))))/((2*l^2*rH^3 + rH)*sqrt(l^2*rH^2 + 1))

Let us perform an expansion in $1/r$ for $r\rightarrow +\infty$:

In [117]:
assume(l > 0)

u = var('u')
assume(u > 0)
s = pi_theta.subs({r: 1/u}).simplify_log()
s = s.taylor(u, 0, 2)
s = s.subs({u: 1/r})
s

3/2*(a^2*l^2*n^2*sin(Th2) - a^2*l^2*sin(Th2))*r + 3/2*(a^2*n^2*sin(Th2) - a^2*sin(Th2))/r + 1/4*(pi*a^2*l*n^2*qf^2*sin(Th2) + 2*pi*a^2*l^3*m*sin(Th2) - pi*a^2*l*pf^2*sin(Th2) + 4*pi*a^2*l*sin(Th2) - 2*(pi*a^2*l^3*m*sin(Th2) + 2*pi*a^2*l*sin(Th2))*n^2 - 3*(pi*a^2*l^3*n^2*sin(Th2) - pi*a^2*l^3*sin(Th2))*rH^2 + 4*(C_1*a^2*n^2 + 2*C_1*a^2*n + C_1*a^2 + 2*(C_1*a^2*l^2*n^2 + 2*C_1*a^2*l^2*n + C_1*a^2*l^2)*rH^2)*sqrt(l^2*rH^2 + 1))/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1))

We consider $\frac{\pi^r_\theta}{(a^2/2)\sin(2\Theta_0)}$:

In [118]:
s1 = (s/(a^2/2*sin(Th2))).expand()
s1

-3/2*pi*l^3*n^2*rH^2/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) - pi*l^3*m*n^2/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) + 3*l^2*n^2*r + 4*C_1*l^2*n^2*rH^2/((2*l^2*rH^2 + 1)*sin(Th2)) + 1/2*pi*l*n^2*qf^2/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) + 3/2*pi*l^3*rH^2/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) + 8*C_1*l^2*n*rH^2/((2*l^2*rH^2 + 1)*sin(Th2)) + pi*l^3*m/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) - 3*l^2*r + 4*C_1*l^2*rH^2/((2*l^2*rH^2 + 1)*sin(Th2)) - 2*pi*l*n^2/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) - 1/2*pi*l*pf^2/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) + 3*n^2/r + 2*C_1*n^2/((2*l^2*rH^2 + 1)*sin(Th2)) + 2*pi*l/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1)) + 4*C_1*n/((2*l^2*rH^2 + 1)*sin(Th2)) - 3/r + 2*C_1/((2*l^2*rH^2 + 1)*sin(Th2))

The term in factor of $C_1$ is

In [119]:
s1.coefficient(C_1)

4*l^2*n^2*rH^2/((2*l^2*rH^2 + 1)*sin(Th2)) + 8*l^2*n*rH^2/((2*l^2*rH^2 + 1)*sin(Th2)) + 4*l^2*rH^2/((2*l^2*rH^2 + 1)*sin(Th2)) + 2*n^2/((2*l^2*rH^2 + 1)*sin(Th2)) + 4*n/((2*l^2*rH^2 + 1)*sin(Th2)) + 2/((2*l^2*rH^2 + 1)*sin(Th2))

It is a constant term, of the type $\tilde{C}_1/\sin(2\Theta_0)$, in agreement with Eq. (4.14).
We remove it from the main term:

In [120]:
s2 = (s1 - s1.coefficient(C_1)*C_1).simplify_full()
s2

1/2*(12*(l^4*n^2 - l^4 + (l^6*n^2 - l^6)*r^2)*rH^4 + 6*(l^2*n^2 - l^2)*r^2 + 18*(l^2*n^2 + (l^4*n^2 - l^4)*r^2 - l^2)*rH^2 + 6*n^2 - sqrt(l^2*rH^2 + 1)*(3*(pi*l^3*n^2 - pi*l^3)*r*rH^2 - (pi*l*n^2*qf^2 + 2*pi*l^3*m - pi*l*pf^2 - 2*(pi*l^3*m + 2*pi*l)*n^2 + 4*pi*l)*r) - 6)/(2*l^4*r*rH^4 + 3*l^2*r*rH^2 + r)

In [121]:
s2.numerator().simplify_full()

12*(l^4*n^2 - l^4 + (l^6*n^2 - l^6)*r^2)*rH^4 + 6*(l^2*n^2 - l^2)*r^2 + 18*(l^2*n^2 + (l^4*n^2 - l^4)*r^2 - l^2)*rH^2 + 6*n^2 - sqrt(l^2*rH^2 + 1)*(3*(pi*l^3*n^2 - pi*l^3)*r*rH^2 - (pi*l*n^2*qf^2 + 2*pi*l^3*m - pi*l*pf^2 - 2*(pi*l^3*m + 2*pi*l)*n^2 + 4*pi*l)*r) - 6

In [122]:
s2.denominator().factor()

2*(2*l^2*rH^2 + 1)*(l^2*rH^2 + 1)*r

Let divide both the numerator and denominator by $r$:

In [123]:
s2n = (s2.numerator()/r).expand()
s2n

12*l^6*n^2*r*rH^4 - 12*l^6*r*rH^4 + 18*l^4*n^2*r*rH^2 + 12*l^4*n^2*rH^4/r - 3*pi*sqrt(l^2*rH^2 + 1)*l^3*n^2*rH^2 - 2*pi*sqrt(l^2*rH^2 + 1)*l^3*m*n^2 - 18*l^4*r*rH^2 - 12*l^4*rH^4/r + pi*sqrt(l^2*rH^2 + 1)*l*n^2*qf^2 + 3*pi*sqrt(l^2*rH^2 + 1)*l^3*rH^2 + 2*pi*sqrt(l^2*rH^2 + 1)*l^3*m + 6*l^2*n^2*r + 18*l^2*n^2*rH^2/r - 4*pi*sqrt(l^2*rH^2 + 1)*l*n^2 - pi*sqrt(l^2*rH^2 + 1)*l*pf^2 - 6*l^2*r - 18*l^2*rH^2/r + 4*pi*sqrt(l^2*rH^2 + 1)*l + 6*n^2/r - 6/r

In [124]:
s2d = (s2.denominator()/r).factor()
s2d

2*(2*l^2*rH^2 + 1)*(l^2*rH^2 + 1)

The coefficient of the term in $r$ is

In [125]:
s = s2n.coefficient(r).factor()
s/s2d

3*l^2*(n + 1)*(n - 1)

This is in agreement with Eq. (4.14).

We remove it:

In [126]:
s3n = (s2n - s*r).simplify_full().expand()
s3n

12*l^4*n^2*rH^4/r - 3*pi*sqrt(l^2*rH^2 + 1)*l^3*n^2*rH^2 - 2*pi*sqrt(l^2*rH^2 + 1)*l^3*m*n^2 - 12*l^4*rH^4/r + pi*sqrt(l^2*rH^2 + 1)*l*n^2*qf^2 + 3*pi*sqrt(l^2*rH^2 + 1)*l^3*rH^2 + 2*pi*sqrt(l^2*rH^2 + 1)*l^3*m + 18*l^2*n^2*rH^2/r - 4*pi*sqrt(l^2*rH^2 + 1)*l*n^2 - pi*sqrt(l^2*rH^2 + 1)*l*pf^2 - 18*l^2*rH^2/r + 4*pi*sqrt(l^2*rH^2 + 1)*l + 6*n^2/r - 6/r

The coefficient of the term in $1/r$ is

In [127]:
s = s3n.coefficient(r^(-1)).factor()
s/s2d

3*(n + 1)*(n - 1)

This is in agreement with Eq. (4.14).

Finally the remaining term is

In [128]:
s4n = (s3n - s/r).simplify_full().expand()
s4n

-3*pi*sqrt(l^2*rH^2 + 1)*l^3*n^2*rH^2 - 2*pi*sqrt(l^2*rH^2 + 1)*l^3*m*n^2 + pi*sqrt(l^2*rH^2 + 1)*l*n^2*qf^2 + 3*pi*sqrt(l^2*rH^2 + 1)*l^3*rH^2 + 2*pi*sqrt(l^2*rH^2 + 1)*l^3*m - 4*pi*sqrt(l^2*rH^2 + 1)*l*n^2 - pi*sqrt(l^2*rH^2 + 1)*l*pf^2 + 4*pi*sqrt(l^2*rH^2 + 1)*l

In [129]:
s4n.factor()

-pi*(3*l^2*n^2*rH^2 + 2*l^2*m*n^2 - n^2*qf^2 - 3*l^2*rH^2 - 2*l^2*m + 4*n^2 + pf^2 - 4)*sqrt(l^2*rH^2 + 1)*l

In [130]:
s = (s4n.factor()/s2d).subs({m: m_rH}).factor()
s

-1/2*pi*(l^4*n^2*rH^4 - l^4*rH^4 + 4*l^2*n^2*rH^2 - n^2*qf^2 - 4*l^2*rH^2 + 4*n^2 + pf^2 - 4)*l/((2*l^2*rH^2 + 1)*sqrt(l^2*rH^2 + 1))

The denominator clearly agrees with Eq. (4.14); the numerator agrees as well:

In [131]:
bool(s.numerator()/(pi*l) == (1 - n^2)*(l^2*rH^2 + 2)^2 - pf^2 + n^2*qf^2)

True

**Conclusion:** we have full agreement with Eq. (4.14).